Setup cell

In [ ]:
!pip install arabic-reshaper python-bidi jdatetime utm --quiet

import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from matplotlib import rcParams
import arabic_reshaper
from bidi.algorithm import get_display
import jdatetime

import geopandas as gpd
from shapely.geometry import Polygon
import folium
from branca.colormap import StepColormap


rcParams['font.family'] = 'DejaVu Sans'

def fa_label(text):
    return get_display(arabic_reshaper.reshape(text))

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 292.1/292.1 kB 9.5 MB/s eta 0:00:00


In [ ]:
from google.colab import drive

drive.mount('/content/drive', force_remount=True)


file_path = '/content/drive/MyDrive/Colab Notebooks/Divar.csv'


df = pd.read_csv(file_path , encoding='utf-8')

Mounted at /content/drive


/tmp/ipython-input-1578516001.py:9: DtypeWarning: Columns (11,27,29,53) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_path , encoding='utf-8')


	بر روی نقشه‌ی جغرافیایی heatmap آگهی‌های هر منطقه را رسم کنید. تراکم آگهی‌ها کدام منطقه بیشتر است؟

Handeling missing values

In [ ]:
print(df[['location_latitude', 'location_longitude']].isna().sum())

location_latitude     344392
location_longitude    344392
dtype: int64


In [ ]:
df_filled = df.copy()


neigh_mean = df_filled.groupby('neighborhood_slug')[['location_latitude', 'location_longitude']].transform('mean')
df_filled['location_latitude'] = df_filled['location_latitude'].fillna(neigh_mean['location_latitude'])
df_filled['location_longitude'] = df_filled['location_longitude'].fillna(neigh_mean['location_longitude'])


city_mean = df_filled.groupby('city_slug')[['location_latitude', 'location_longitude']].transform('mean')
df_filled['location_latitude'] = df_filled['location_latitude'].fillna(city_mean['location_latitude'])
df_filled['location_longitude'] = df_filled['location_longitude'].fillna(city_mean['location_longitude'])

In [ ]:
print(df_filled[['location_latitude', 'location_longitude']].isna().sum())

location_latitude     2
location_longitude    2
dtype: int64


In [ ]:
df_filled = df_filled.dropna(subset=['location_latitude', 'location_longitude'])

In [ ]:
print(df_filled[['location_latitude', 'location_longitude']].isna().sum())

location_latitude     0
location_longitude    0
dtype: int64


In [ ]:
min_lat, max_lat = df_filled['location_latitude'].min(), df_filled['location_latitude'].max()
min_lon, max_lon = df_filled['location_longitude'].min(), df_filled['location_longitude'].max()


lat_step = 0.05
lon_step = 0.05

polygons, counts, ids = [], [], []
lat_bins = pd.interval_range(min_lat, max_lat, freq=lat_step)
lon_bins = pd.interval_range(min_lon, max_lon, freq=lon_step)
cell_id = 0

for lat_bin in lat_bins:
    for lon_bin in lon_bins:
        count = df_filled[
            (df_filled['location_latitude'].between(lat_bin.left, lat_bin.right)) &
            (df_filled['location_longitude'].between(lon_bin.left, lon_bin.right))
        ].shape[0]
        if count > 0:
            polygons.append(Polygon([
                (lon_bin.left, lat_bin.left),
                (lon_bin.right, lat_bin.left),
                (lon_bin.right, lat_bin.right),
                (lon_bin.left, lat_bin.right)
            ]))
            counts.append(count)
            ids.append(cell_id)
            cell_id += 1

gdf = gpd.GeoDataFrame({'cell_id': ids, 'count': counts, 'geometry': polygons}, crs="EPSG:4326")


max_count = gdf['count'].max()
step_bins = [0, max_count*0.2, max_count*0.4, max_count*0.6, max_count*0.8, max_count]
blue_steps = StepColormap(
    colors=['#deebf7', '#9ecae1', '#6baed6', '#4292c6', '#0868ac', '#08306b'],
    vmin=0, vmax=max_count,
    index=step_bins,
    caption='تعداد آگهی‌ها'
)

m = folium.Map(
    location=[df_filled['location_latitude'].mean(), df_filled['location_longitude'].mean()],
    zoom_start=6
)

folium.GeoJson(
    gdf,
    style_function=lambda feature: {
        'fillColor': blue_steps(feature['properties']['count']),
        'color': 'black',
        'weight': 0.2,
        'fillOpacity': 0.7,
    },
    tooltip=folium.GeoJsonTooltip(fields=['count'], aliases=['تعداد آگهی‌ها:'])
).add_to(m)

blue_steps.add_to(m)

m
